# DQN v2

#### This version implements DQN with Keras
#### Findings:
Smaller NET then v1 does not work

In [37]:
import tensorflow as tf
from tensorflow.keras import layers
from tensorflow.keras.utils import to_categorical
import gym
from gym import spaces
from gym.utils import seeding
from gym import wrappers

from tqdm.notebook import tqdm
from collections import deque
import numpy as np
import random
from matplotlib import pyplot as plt
from sklearn.preprocessing import MinMaxScaler
import joblib

import io
import base64
from IPython.display import HTML, Video


In [57]:
class DQN:
    def __init__(self, env=None, replay_buffer_size=1000, action_size=2):
        self.replay_buffer = deque(maxlen=replay_buffer_size)

        self.action_size = action_size

        # Hyperparameters
        self.gamma = 0.95           # Discount rate
        self.epsilon = 1.0          # Exploration rate
        self.epsilon_min = 0.001      # Minimal exploration rate (epsilon-greedy)
        self.epsilon_decay = 0.95    # Decay rate for epsilon
        self.update_rate = 5       # Number of steps until updating the target network
        self.batch_size = 100
        self.learning_rate = 5e-4
        
        # Construct DQN models
        self.model = self._build_model()
        self.target_model = self._build_model()
        self.target_model.set_weights(self.model.get_weights())
        self.model.summary()
        self.env = env
        self.action_size = action_size

        self.scaler = None

    def _build_model(self):
        model = tf.keras.Sequential()
        
        model.add(tf.keras.Input(shape=(4,)))
        model.add(layers.Dense(512, activation = 'relu'))
        model.add(layers.Dense(256, activation = 'relu'))
        model.add(layers.Dense(128, activation = 'relu'))
        model.add(layers.Dense(self.action_size, activation = 'linear'))
        # model.compile(optimizer = RMSprop(lr = self.lr, rho = 0.95, epsilon = 0.01), loss = "mse", metrics = ['accuracy'])
        
        optimizer = tf.keras.optimizers.Adam(learning_rate=self.learning_rate)
        # model.compile(loss='mse', optimizer=tf.keras.optimizers.RMSprop(lr = self.learning_rate, rho = 0.95, epsilon = 0.01), metrics = ['accuracy'])
        model.compile(loss='mse', optimizer=optimizer, metrics = ['accuracy'])
        return model

    def _min_max(self):
        """Run some steps to get data to do MINMAX scale """
        state_arr = []
        state_arr.append(self.env.observation_space.high)
        state_arr[0][1], state_arr[0][3] = 0,0
        state_arr.append(self.env.observation_space.low)
        state_arr[1][1], state_arr[1][3] = 0,0
        state = self.env.reset()
        for i in range(1000):
            random_action = self.env.action_space.sample()
            next_state, reward, done, info = self.env.step(random_action)
            state_arr.append(next_state)
            if done:
                state = self.env.reset()

        state_arr = np.array(state_arr)
        self.scaler = MinMaxScaler()
        self.scaler.fit(state_arr)
        # print(self.scaler.data_max_)
        # print(self.scaler.data_min_)

    def _get_scaled_state(self, state):
        return state
        # return self.scaler.transform(state.reshape(1,-1)).flatten()

    #
    # Trains the model using randomly selected experiences in the replay memory
    #
    def _train(self):
        X, y = [], []
        # state, action, reward, next_state, done 
        # create the targets 
        if self.batch_size > len(self.replay_buffer):
            return
        minibatch = random.sample(self.replay_buffer, self.batch_size)
        mb_arr = np.array(minibatch, dtype=object)

        next_state_arr = np.stack(mb_arr[:,3])
        future_qvalues = self.target_model.predict(next_state_arr, verbose=0)

        state_arr = np.stack(mb_arr[:,0])
        qvalues = self.model.predict(state_arr, verbose=0)

        for index, (state, action, reward, next_state, done) in enumerate(minibatch):
            if done == True:
                q_target = reward
            else:
                q_target = reward + self.gamma * np.max(future_qvalues[index])

            q_curr = qvalues[index]
            q_curr[action] = q_target                
            X.append(state)
            y.append(q_curr)

        # Perform gradient step
        X, y = np.array(X), np.array(y)
        history = self.model.fit(X, y, batch_size = self.batch_size, shuffle = False, verbose=0)
        # history = self.model.fit(X, y, epochs=1, verbose=0)
        # print(f"Loss: {history.history['loss']}  ")


    def learn(self, total_steps=None):
        #create scaler
        self._min_max()
        current_episode = 0
        total_reward = 0
        rewards = [0]
        current_step = 0
        while current_step < total_steps:
            current_episode += 1
            state = self.env.reset()
            state = self._get_scaled_state(state)
            total_reward = 0
            done = False
            while done != True:
                current_step +=1
                # e-greedy
                if np.random.random() > (1 - self.epsilon):
                    action = random.randrange(self.action_size)
                else:
                    model_predict = self.model.predict(np.array([state]), verbose=0)
                    action = np.argmax(model_predict)

                # step
                next_state, reward, done, info = self.env.step(action)
                total_reward += reward

                next_state = self._get_scaled_state(next_state)

                # add to buffer
                self.replay_buffer.append((state, action, reward, next_state, done))

                if current_step>10 and current_step % self.update_rate == 0:
                    print(f"epsilon:{self.epsilon} step:{current_step} episode:{current_episode} last_score {rewards[-1]} ")
                    self._train()
                    # update target
                    self.target_model.set_weights(self.model.get_weights())
                
                state = next_state

                # update epsilon every 100 steps 
                if current_step % 20 == 0:
                    if self.epsilon > self.epsilon_min:
                        self.epsilon *= self.epsilon_decay

            rewards.append(total_reward)

    #
    # Loads a saved model
    #
    def load(self, name):
        self.model.load_weights(name)
        self.scaler = joblib.load(name+".scaler") 

    #
    # Saves parameters of a trained model
    #
    def save(self, name):
        self.model.save_weights(name)
        joblib.dump(self.scaler, name+".scaler") 

    def play(self, state):
        state = self._get_scaled_state(state)
        return np.argmax(self.model.predict(np.array([state]), verbose=0)[0])

In [58]:
env = gym.make('CartPole-v1')

model = DQN(env=env, replay_buffer_size=10_000, action_size=2)
model.learn(total_steps=6_000)
env.close()

Model: "sequential_36"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense_144 (Dense)           (None, 512)               2560      
                                                                 
 dense_145 (Dense)           (None, 256)               131328    
                                                                 
 dense_146 (Dense)           (None, 128)               32896     
                                                                 
 dense_147 (Dense)           (None, 2)                 258       
                                                                 
Total params: 167,042
Trainable params: 167,042
Non-trainable params: 0
_________________________________________________________________
epsilon:1.0 step:15 episode:1 last_score 0 
epsilon:1.0 step:20 episode:1 last_score 0 
epsilon:0.95 step:25 episode:1 last_score 0 
epsilon:0.95 step:30 episode:2 last_score 26.0

In [59]:
model.save("./alt/DQN_v2.h5")

In [60]:
eval_env = gym.make('CartPole-v1')
model = DQN(env=eval_env, replay_buffer_size=10_000, action_size=2)
model.load("./alt/DQN_v2.h5")
eval_env = wrappers.Monitor(eval_env, "./alt/gym-results", force=True)
state = eval_env.reset()
total_reward = 0
for _ in range(1000):
    action = model.play(state)
    observation, reward, done, info = eval_env.step(action)
    total_reward +=reward
    state = observation
    if done: 
        break
print(f"Total reward {total_reward}")
eval_env.close()

Model: "sequential_38"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense_152 (Dense)           (None, 512)               2560      
                                                                 
 dense_153 (Dense)           (None, 256)               131328    
                                                                 
 dense_154 (Dense)           (None, 128)               32896     
                                                                 
 dense_155 (Dense)           (None, 2)                 258       
                                                                 
Total params: 167,042
Trainable params: 167,042
Non-trainable params: 0
_________________________________________________________________
Total reward 439.0


In [16]:

# def _min_max(env):
#     """Run some steps to get data to do MINMAX scale """
#     state_arr = []
#     state_arr.append(env.observation_space.high)
#     state_arr[0][1], state_arr[0][3] = 0,0
#     state_arr.append(env.observation_space.low)
#     state_arr[1][1], state_arr[1][3] = 0,0
#     state = env.reset()
#     for i in range(1000):
#         random_action = env.action_space.sample()
#         next_state, reward, done, info = env.step(random_action)
#         state_arr.append(next_state)
#         if done:
#             state = env.reset()

#     state_arr = np.array(state_arr)

#     print(state_arr)
#     scaler = MinMaxScaler()
#     scaler.fit(state_arr)
#     print("Max ",scaler.data_max_)
#     print("Min ", scaler.data_min_)
#     return scaler

# env = gym.make('CartPole-v1')
# scaler = _min_max(env)
# state = env.reset()
# print(state)
# state =  scaler.transform(state.reshape(1, -1)).flatten()
# print(state)


[[ 4.8000002e+00  0.0000000e+00  4.1887903e-01  0.0000000e+00]
 [-4.8000002e+00  0.0000000e+00 -4.1887903e-01  0.0000000e+00]
 [-4.5489166e-03 -2.4116948e-01 -4.1077949e-02  3.0230245e-01]
 ...
 [ 5.0607350e-02  1.7593256e-01 -8.8660561e-02 -4.2944443e-01]
 [ 5.4126002e-02  3.7219086e-01 -9.7249448e-02 -7.4870765e-01]
 [ 6.1569817e-02  5.6851023e-01 -1.1222360e-01 -1.0703416e+00]]
Max  [4.8        2.2215695  0.41887903 2.1663814 ]
Min  [-4.8        -1.4063605  -0.41887903 -2.5751066 ]
[ 0.0172858   0.00332159 -0.03439883  0.01944862]
[0.5018006  0.38856372 0.45893943 0.54720277]
